In [1]:
import pandas as pd
import requests 
import json
from datetime import datetime, timezone, timedelta
import time

In [2]:
df1 = pd.read_csv("D:\GitHub\Incursion-Damage-Mods\webcrawler\HeatSinkOutput.csv")
df2 = pd.read_csv("D:\GitHub\Incursion-Damage-Mods\webcrawler\MagStabOutput.csv")
df3 = pd.read_csv("D:\GitHub\Incursion-Damage-Mods\webcrawler\GyroStabOutput.csv")

df_merge = pd.concat([df1, df2], ignore_index=True)
df_merge = pd.concat([df_merge, df3], ignore_index=True)
df_merge

ID        CPU    Damage  \
0     https://mutaplasmid.space/module/1041934256024/  16.448000  1.132454   
1     https://mutaplasmid.space/module/1042206514258/  16.448000  1.136845   
2     https://mutaplasmid.space/module/1039904814352/  16.574000  1.129811   
3     https://mutaplasmid.space/module/1036718439343/  17.988000  1.128422   
4     https://mutaplasmid.space/module/1043384985240/  18.030000  1.110682   
...                                               ...        ...       ...   
1020  https://mutaplasmid.space/module/1037349012180/  38.824499  1.108938   
1021  https://mutaplasmid.space/module/1043629929133/  40.737000  1.119756   
1022  https://mutaplasmid.space/module/1043541933325/  41.031000  1.086624   
1023  https://mutaplasmid.space/module/1039022021026/  44.286000  1.117292   
1024  https://mutaplasmid.space/module/1043603958614/  44.538000  1.117908   

           ROF   DPS  Price Flag1  Flag2  \
0     0.872645  29.8   14.9     M    NaN   
1     0.877807  29.5  217.0     M    NaN   
2     0.910559  24.1   11.0     M    NaN   
3     0.895785  26.0  217.0     M    NaN   
4     0.876027  26.8    1.0     M    NaN   
...        ...   ...    ...   ...    ...   
1020  0.887751  24.9   50.0   NaN    NaN   
1021  0.892539  25.5   55.0   NaN    NaN   
1022  0.888109  22.4   30.0   NaN    NaN   
1023  0.892360  25.2   50.0   NaN    NaN   
1024  0.873117  28.0  300.0   NaN    NaN   

                                                Extract     Unit   Contract  
0     ESI  Contract 198788610  Imperial Navy Heat Si...  billion  198788610  
1     ESI  Contract 198568945  Imperial Navy Heat Si...  billion  198568945  
2     ESI  Contract 198924134  Imperial Navy Heat Si...  billion  198924134  
3     ESI  Contract 198568945  Imperial Navy Heat Si...  billion  198568945  
4     ESI  Contract 198547317  Imperial Navy Heat Si...  billion  198547317  
...                                                 ...      ...        ...  
1020  ESI  Contract 198250370  Gyrostabilizer II  Gr...  million  198250370  
1021  ESI  Contract 198674205  Gyrostabilizer II  Un...  million  198674205  
1022  ESI  Contract 198345579  Gyrostabilizer II  Un...  million  198345579  
1023  ESI  Contract 197964156  Gyrostabilizer II  Un...  million  197964156  
1024  ESI  Contract 198570069  Gyrostabilizer II  Un...  million  198570069  

[1025 rows x 11 columns]

In [3]:
url = "https://esi.evetech.net/latest/universe/regions/"

response = requests.get(url)
region_ids = response.json()
print(f"Regions to scan: {len(region_ids)}")

Regions to scan: 112


In [4]:
contracts = []
for region_id in region_ids:
    total_pages = 1
    current_page = 1
    base_url = "https://esi.evetech.net/latest/contracts/public/{}/".format(region_id)
    params = {"datasource": "tranquility", "page": current_page}
    
    while params["page"] <= total_pages:
        print(base_url)
        print(params)
        response = requests.get(base_url, params=params)
        print(response.headers)
        print(response)
        if total_pages == 1:
            total_pages = int(response.headers.get("X-Pages"))
            
        if response.status_code == 200:
            raw_contracts = response.json()
            item_exchange_contracts = [contract for contract in raw_contracts if contract["type"] == "item_exchange"]
            contracts.extend(item_exchange_contracts)
            params["page"] += 1
        else:
            raise ValueError("Unexpected API Response")
        if "ETag" not in params:
            params["ETag"] = response.headers.get("ETag").strip('\"')    
        

pd.json_normalize(contracts).to_parquet("./api_database/contracts.parquet")

https://esi.evetech.net/latest/contracts/public/10000001/
{'datasource': 'tranquility', 'page': 1}
{'Date': 'Tue, 12 Dec 2023 10:23:24 GMT', 'Content-Type': 'application/json; charset=UTF-8', 'Transfer-Encoding': 'chunked', 'Connection': 'keep-alive', 'Access-Control-Allow-Credentials': 'true', 'Access-Control-Allow-Headers': 'Content-Type,Authorization,If-None-Match,X-User-Agent', 'Access-Control-Allow-Methods': 'GET,HEAD,OPTIONS', 'Access-Control-Allow-Origin': '*', 'Access-Control-Expose-Headers': 'Content-Type,Warning,ETag,X-Pages,X-ESI-Error-Limit-Remain,X-ESI-Error-Limit-Reset', 'Access-Control-Max-Age': '600', 'Allow': 'GET,HEAD,OPTIONS', 'Cache-Control': 'public', 'Content-Encoding': 'gzip', 'Etag': '"cc316a404273d484c916fa7dfba73b4905203cd8d0782f44b9770d06"', 'Expires': 'Tue, 12 Dec 2023 10:47:50 GMT', 'Last-Modified': 'Tue, 12 Dec 2023 10:17:50 GMT', 'Strict-Transport-Security': 'max-age=31536000', 'Vary': 'Accept-Encoding', 'X-Esi-Error-Limit-Remain': '100', 'X-Esi-Error-Lim

In [6]:
df_contracts = pd.read_parquet("./api_database/contracts.parquet")[["contract_id", "date_issued"]]

known_abyssal_contracts = pd.read_parquet("./api_database/item_stats.parquet")
known_abyssal_contracts_agg = known_abyssal_contracts.groupby("contract_id", as_index=False).agg({
    "item_id": "nunique"
}).rename(columns={"item_id":"abyssal_count"})

df_contracts = df_contracts.merge(known_abyssal_contracts_agg,how="left", on ="contract_id")
df_contracts["date_issued"] = pd.to_datetime(df_contracts["date_issued"])
df_contracts = df_contracts[(df_contracts["date_issued"] > (pd.to_datetime(datetime.utcnow() - timedelta(days=1)).tz_localize("UTC"))) | (df_contracts["abyssal_count"] > 0)][["contract_id"]]

last_run_items = pd.read_parquet("./api_database/contract_items.parquet")
last_run_contracts = last_run_items.groupby("contract_id", as_index=False).agg({
    "updated_at": "max"
})

contracts_to_scan = df_contracts.merge(last_run_contracts, how="left", on="contract_id")
contracts_to_scan = contracts_to_scan[(contracts_to_scan["updated_at"] < (pd.to_datetime("today") + pd.DateOffset(hours=-12))) | (contracts_to_scan["updated_at"].isna())] ["contract_id"].drop_duplicates(keep="first").tolist()

last_run_items = last_run_items.merge(df_contracts[["contract_id"]].drop_duplicates(keep="first"), how="inner", on="contract_id")
contracts_scanned = last_run_items[last_run_items["updated_at"] > (pd.to_datetime("today") + pd.DateOffset(hours=-12))]

In [7]:
len(contracts_to_scan)

5940

In [151]:
items = []
contract_count = 0
print (len(contracts_to_scan))
for contract_id in contracts_to_scan:
    total_pages = 1
    page = 1
    while page <= total_pages:
        contract_count += 1
        base_url = "https://esi.evetech.net/latest/contracts/public/items/{}/".format(contract_id)
        params = {"datasource": "tranquility", "page": page}
                
        print(base_url)
        print(params)
        print(contract_count)
        response = requests.get(base_url, params=params)
        print(response.headers)
        print(response)
        if (total_pages == 1) & (response.headers.get("X-Pages") != None):
            total_pages = int(response.headers.get("X-Pages"))
            print(total_pages)
        
        if response.status_code == 200:
            if response.text != "":
                raw_contract_items = response.json()
                contract_items = [contract_item for contract_item in raw_contract_items]
                print(f"Items found: {len(contract_items)}")
                for contract_item in contract_items:
                    contract_item["contract_id"] = contract_id
                    contract_item["updated_at"] = datetime.utcnow()
                items.extend(contract_items)
        else:
            if int(response.headers.get("X-Esi-Error-Limit-Remain", 100)) < 20:
                break
            elif int(response.headers.get("X-Esi-Error-Limit-Remain", 50)) < 50:
                time.sleep(60)
        page += 1

contracts_scanned = pd.concat([contracts_scanned, pd.json_normalize(items)],ignore_index=True)
contracts_scanned.to_parquet("./api_database/contract_items.parquet")


6136
https://esi.evetech.net/latest/contracts/public/items/198908935/
{'datasource': 'tranquility', 'page': 1}
1
{'Date': 'Sun, 10 Dec 2023 08:33:21 GMT', 'Content-Type': 'application/json; charset=UTF-8', 'Content-Length': '98', 'Connection': 'keep-alive', 'Access-Control-Allow-Credentials': 'true', 'Access-Control-Allow-Headers': 'Content-Type,Authorization,If-None-Match,X-User-Agent', 'Access-Control-Allow-Methods': 'GET,HEAD,OPTIONS', 'Access-Control-Allow-Origin': '*', 'Access-Control-Expose-Headers': 'Content-Type,Warning,ETag,X-Pages,X-ESI-Error-Limit-Remain,X-ESI-Error-Limit-Reset', 'Access-Control-Max-Age': '600', 'Allow': 'GET,HEAD,OPTIONS', 'Cache-Control': 'public', 'Etag': '"93d26d913732fd0af0db375c383ae894f32734d4468f478d3d5391db"', 'Expires': 'Sun, 10 Dec 2023 08:39:04 GMT', 'Last-Modified': 'Sun, 10 Dec 2023 07:39:04 GMT', 'Strict-Transport-Security': 'max-age=31536000', 'X-Esi-Error-Limit-Remain': '100', 'X-Esi-Error-Limit-Reset': '39', 'X-Esi-Request-Id': 'c694725a-de

In [160]:
known_abyssal_contracts = pd.read_parquet("./api_database/item_stats.parquet")
known_abyssal_contracts_agg = known_abyssal_contracts.groupby(["contract_id"], as_index=False).agg({
    "item_id": "nunique"
}).rename(columns={"item_id":"item_id_count"})

# Clean up affteragg data TODO
contract_items = pd.read_parquet("./api_database/contract_items.parquet")
contract_items = contract_items.merge(known_abyssal_contracts_agg, how="left", on=["contract_id"])
contract_items_to_scan = contract_items[(contract_items["item_id_count"].isna()) & (contract_items["item_id"].notna())]
contract_items_to_scan["item_id"] = contract_items_to_scan["item_id"].astype("int64")
contract_items_to_scan["item_idtype_id"] = contract_items_to_scan["type_id"].astype("int64")

contract_items_scanned = contract_items[(contract_items["item_id_count"].notna())]
# contract_items_scanned = known_abyssal_contracts.merge(contract_items_scanned[["contract_id"]].drop_duplicates(keep="first"), how="inner", on="contract_id")
contract_items_scanned

C:\Users\Man\AppData\Local\Temp\ipykernel_20872\1597708568.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  contract_items_to_scan["item_id"] = contract_items_to_scan["item_id"].astype("int64")
C:\Users\Man\AppData\Local\Temp\ipykernel_20872\1597708568.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  contract_items_to_scan["item_idtype_id"] = contract_items_to_scan["type_id"].astype("int64")


is_included       item_id  quantity     record_id  type_id  \
0              True  1.041116e+12       1.0  4.250377e+09  49730.0   
1              True  1.041116e+12       1.0  4.250377e+09  49730.0   
2              True  1.041116e+12       1.0  4.250377e+09  49730.0   
3              True  1.041116e+12       1.0  4.250377e+09  49730.0   
4              True  1.041116e+12       1.0  4.250377e+09  49730.0   
...             ...           ...       ...           ...      ...   
175727         True  1.043671e+12       1.0  4.255643e+09  49722.0   
175729         True  1.035098e+12       1.0  4.255644e+09  49730.0   
175892         True  1.043408e+12       1.0  4.255657e+09  49730.0   
176009         True  1.043639e+12       1.0  4.255679e+09  49730.0   
176014         True  1.043639e+12       1.0  4.255680e+09  49726.0   

        contract_id                 updated_at is_blueprint_copy  \
0         198751555 2023-12-10 06:11:16.134174              None   
1         198751555 2023-12-10 06:11:16.134174              None   
2         198751555 2023-12-10 06:11:16.134174              None   
3         198751555 2023-12-10 06:11:16.134174              None   
4         198751555 2023-12-10 06:11:16.134174              None   
...             ...                        ...               ...   
175727    198949492 2023-12-10 09:49:13.816374              None   
175729    198949523 2023-12-10 09:49:16.161986              None   
175892    198950105 2023-12-10 09:50:59.250471              None   
176009    198951092 2023-12-10 09:52:17.935631              None   
176014    198951150 2023-12-10 09:52:23.657129              None   

        material_efficiency  runs  time_efficiency  item_id_count  
0                       NaN   NaN              NaN            1.0  
1                       NaN   NaN              NaN            1.0  
2                       NaN   NaN              NaN            1.0  
3                       NaN   NaN              NaN            1.0  
4                       NaN   NaN              NaN            1.0  
...                     ...   ...              ...            ...  
175727                  NaN   NaN              NaN            1.0  
175729                  NaN   NaN              NaN            1.0  
175892                  NaN   NaN              NaN            1.0  
176009                  NaN   NaN              NaN            1.0  
176014                  NaN   NaN              NaN            1.0  

[1372 rows x 12 columns]

In [161]:
item_stats = []

for index, row in contract_items_to_scan.iterrows():
    if row["type_id"] in [49726, 49722, 49730]:
        base_url = f"https://esi.evetech.net/latest/dogma/dynamic/items/{row['type_id']}/{row['item_id']}/"
        params = {"datasource": "tranquility"}
        print(base_url)
        print(params)
        response = requests.get(base_url, params=params)
        print(response.headers)
        print(response)

        if response.status_code == 200:
            row_info = response.json()
            dogma_details = []
            dogma_details = [mod for mod in row_info["dogma_attributes"] if mod["attribute_id"] in [50,64,204]]
            for mod in dogma_details:
                mod["contract_id"] = row["contract_id"]
                mod["type_id"] = row["type_id"]
                mod["item_id"] = row["item_id"]
            item_stats.extend(dogma_details)
        else:
            if int(response.headers["X-Esi-Error-Limit-Remain"]) < 20:
                break
            elif int(response.headers["X-Esi-Error-Limit-Remain"]) < 50:
                time.sleep(60)
                
df_pivoted = pd.json_normalize(item_stats).pivot(index=['contract_id', 'type_id', 'item_id'], columns='attribute_id', values='value').reset_index()
df_pivoted = df_pivoted.rename_axis(None, axis=1)
df_pivoted = df_pivoted.rename(columns={50: "CPU", 64: "Damage" , 204:"ROF"})
output = pd.concat([contract_items_scanned, df_pivoted], ignore_index=True).drop_duplicates(keep="first")
 		
output.to_parquet("./api_database/item_stats.parquet")
output


https://esi.evetech.net/latest/dogma/dynamic/items/49726.0/1039867699192/
{'datasource': 'tranquility'}
{'Date': 'Sun, 10 Dec 2023 10:52:19 GMT', 'Content-Type': 'application/json; charset=utf-8', 'Content-Length': '21', 'Connection': 'keep-alive', 'Access-Control-Allow-Credentials': 'true', 'Access-Control-Allow-Headers': 'Content-Type,Authorization,If-None-Match,X-User-Agent', 'Access-Control-Allow-Origin': '*', 'Access-Control-Expose-Headers': 'Content-Type,Warning,ETag,X-Pages,X-ESI-Error-Limit-Remain,X-ESI-Error-Limit-Reset', 'Access-Control-Max-Age': '600', 'Content-Language': 'en-us', 'Strict-Transport-Security': 'max-age=31536000', 'Vary': 'Accept-Language', 'X-Esi-Error-Limit-Remain': '99', 'X-Esi-Error-Limit-Reset': '41'}
<Response [404]>
https://esi.evetech.net/latest/dogma/dynamic/items/49726.0/1039867699192/
{'datasource': 'tranquility'}
{'Date': 'Sun, 10 Dec 2023 10:52:20 GMT', 'Content-Type': 'application/json; charset=utf-8', 'Content-Length': '21', 'Connection': 'keep-

KeyboardInterrupt: 